# Examples - non-dilatable $d$-parameter $C_{0}$-semigroups #

This notebook provides supplementary material to the research paper <https://doi.org/10.48550/arXiv.2210.02353>.

In §5.3 a construction is given which yields for any $d \geq 2$
a $d$-parameter $C_{0}$-semigroup, $T$ satisfying:

- $T$ is contractive (equivalently its marginals $T_{i}$ are for each $i$);
- the generator $A_{i}$ of $T_{i}$ has strictly negative spectral bound for each $i$;

and such that $T$ is __not__ **completely dissipative**.
Thus by the classification Theorem (Thm 1.1), $T$ does not have a regular unitary dilation.

This Notebook demonstrates this general result empirically.

In [ ]:
import os;
import sys;

# NOTE: need this to force jupyter to reload imports:
for key in list(sys.modules.keys()):
    if key.startswith('src.'):
        del sys.modules[key];

os.chdir(os.path.dirname(_dh[0]));
sys.path.insert(0, os.getcwd());

from src.examples_dilations import *;
np.random.seed(7098123); # for repeatability

In [ ]:
# User input:
N = 4; # dimension of the Hilbert space.
d = 4;

# If you ensure that the failure of S_{T,K} >= 0 only occurs for K = {1,2,...,d}
# + you want S_TK > 0 (strictly) for all K ≠ {1,2,...,d}:
alpha = 1/math.sqrt(d - 0.5);

# If you ensure that the failure of S_{T,K} >= 0 only occurs for K = {1,2,...,d}
# alpha = 1/math.sqrt(d - 1);

# Otherwise:
# alpha = 1;

In [ ]:
# create the generators `A_i` of the marginal semigroups `T_i`:`
A = [
    generate_semigroup_generator(
        shape    = [N, N],
        rational = True,
        base     = 100,
        alpha    = alpha,
    )
    for _ in range(d)
];

data = [];
for i, A_i in enumerate(A):
    omega_Re = spec_bounds((1/2)*(A_i + A_i.T.conj()));
    omega = spec_bounds(A_i);
    data.append((i+1, omega, True if (omega_Re <= 0) else False));

repr = tabulate(
    tabular_data = data,
    headers      = ['i', 'spec bound of A_i', 'A_i dissipative (<==> T_i contractive)?'],
    showindex    = False,
    floatfmt = '.6f',
    colalign = ['center', 'center', 'center'],
    tablefmt     = 'simple',
);
print(f'\nThe marginal semigroups T_i and their generators A_i:\n\n{repr}');

In [ ]:
# compute the dissipation operators `S_TK` for each `K ⊆ {1,2,...,d}``:
S, beta_T = dissipation_operators(shape=[N, N], A=A);

repr = tabulate(
    tabular_data = [
        (K, b, True if b >= -MACHINE_EPS else False)
        for K, S_TK, b in sorted(S, key=lambda x: (len(x[0]), x[0]) )
    ],
    headers      = ['K', 'min σ(S_{T,K})', 'S_{T,K} >= 0?'],
    showindex    = False,
    floatfmt = '.6f',
    colalign = ['center', 'center', 'center'],
    tablefmt     = 'simple',
);
print(f'\nDissipation operators:\n\n{repr}');

In [ ]:
# Display summary:
print('')
print(f'β_T = min_K min σ(S_{{T,K}}) = {beta_T:.6f}');
if beta_T == 0:
    print('⟹ T is compeletely dissipative.');
    print('⟹ (by Thm 1.1) T has a regular unitary dilation.');
elif beta_T > 0:
    print('⟹ T is compeletely super dissipative.');
    print('⟹ (by Thm 1.1) T has a regular unitary dilation.');
else:
    print('⟹ T is not compeletely dissipative.');
    print('⟹ (by Thm 1.1) T does not have a regular unitary dilation.');